In [1]:
%load_ext autoreload
%autoreload 2

import pandas as pd
import geopandas as gpd
import numpy as np
import plotly.express as px
import statsmodels
from Transit_Quality_Study.transit_quality_study.config import processed_data_dir
from Transit_Quality_Study.transit_quality_study.custom_funcs import *

# Preparing Final Table
First, let's make all our results into one pretty table

In [2]:
# Get all tables
stop_data = gpd.read_parquet(processed_data_dir / 'stop_data.parquet')
stop_frequency = pd.read_parquet(processed_data_dir / 'stop_frequency.parquet')
stop_max_density = pd.read_parquet(processed_data_dir / 'stop_max_density.parquet')
stop_walkable_routes = pd.read_parquet(processed_data_dir / 'stop_walkable_routes.parquet')
scores = [stop_frequency, stop_max_density, stop_walkable_routes]
stop_data = stop_data.join(scores, how='left')

Areas without a population (such as parks and commercial areas) do not have an income. Let's set it to the mean.

In [41]:
stop_data

stop_name                   route_id  \
stop_code                                                                    
10118                         Station Angrignon                        [1]   
10120                              Station Monk                        [1]   
10122                         Station Jolicoeur                        [1]   
10124                            Station Verdun                        [1]   
10126                       Station De l'Église                        [1]   
...                                         ...                        ...   
62373           Henri-Bourassa / de l'Esplanade       [380, 171, 164, 135]   
62374      Henri-Bourassa / du Bois-de-Boulogne  [380, 171, 164, 135, 180]   
62375                 Saint-Laurent / Lighthall                       [69]   
62376                           Hickmore / Mega                      [100]   
62383                Transcanadienne / Tecumseh                      [216]   

                                                  route_name   stop_lat  \
stop_code                                                                 
10118                                    [1 Ligne 1 - Verte]  45.446466   
10120                                    [1 Ligne 1 - Verte]  45.451158   
10122                                    [1 Ligne 1 - Verte]  45.457010   
10124                                    [1 Ligne 1 - Verte]  45.459441   
10126                                    [1 Ligne 1 - Verte]  45.461894   
...                                                      ...        ...   
62373      [380 Henri-Bourassa, 171 Henri-Bourassa, 164 D...  45.547323   
62374      [380 Henri-Bourassa, 171 Henri-Bourassa, 164 D...  45.537554   
62375                                             [69 Gouin]  45.550630   
62376                                         [100 Crémazie]  45.476435   
62383                                  [216 Transcanadienne]  45.472044   

            stop_lon  location_type                    geometry          id  \
stop_code                                                                     
10118     -73.603118              1  POINT (-73.60312 45.44647)  24663382.0   
10120     -73.593242              1  POINT (-73.59324 45.45116)  24661003.0   
10122     -73.581691              1  POINT (-73.58169 45.45701)  24661023.0   
10124     -73.572021              1  POINT (-73.57202 45.45944)  24661179.0   
10126     -73.567074              1  POINT (-73.56707 45.46189)  24661222.0   
...              ...            ...                         ...         ...   
62373     -73.672934              0  POINT (-73.67293 45.54732)  24662522.0   
62374     -73.679091              0  POINT (-73.67909 45.53755)  24662544.0   
62375     -73.671607              0  POINT (-73.67161 45.55063)  24662525.0   
62376     -73.693871              0  POINT (-73.69387 45.47644)  24663419.0   
62383     -73.810659              0  POINT (-73.81066 45.47204)  24663151.0   

           Area (sq km)  Population   Dwellings   Households   Density  \
stop_code                                                                
10118            0.9907          0.0         0.0          0.0      0.0   
10120            0.0526        564.0       276.0        258.0  10722.4   
10122            0.0772        474.0       256.0        244.0   6139.9   
10124            0.0670       1003.0       572.0        551.0  14970.1   
10126            0.1247       1066.0       648.0        619.0   8548.5   
...                 ...          ...         ...          ...      ...   
62373            0.0712        540.0       303.0        285.0   7584.3   
62374            0.0599        656.0       300.0        288.0  10951.6   
62375            0.0952        583.0       276.0        256.0   6123.9   
62376           15.9573        467.0       203.0        194.0     29.3   
62383            5.1553       1191.0       389.0        374.0    231.0   

             Income  index_right  ntrips  Max_Density  w

Next, let's remove all outliers. I will remove all stops with $z \geq 3$

In [4]:
stop_scores = stop_data[['Density', 'Income', 'ntrips', 'Max_Density', 'walkable_routes']]

# Create a Z score table
stop_scores_z = z_score(stop_scores)
# Let's take the index of the remaining scores
indices = remove_outliers(stop_scores_z, threshold = 3).index
stop_scores = stop_scores[stop_scores.index.isin(indices)]
stop_scores

Density    Income  ntrips  Max_Density  walkable_routes
stop_code                                                         
10452          0.0       0.0    2865       8089.3                2
10454       8089.3   63200.0    2865       8089.3                1
10534      21422.2   36800.0    3150      24666.7               10
10536        952.5   41600.0    3150      24666.7                5
10538      24666.7   35600.0    3150      24666.7                5
...            ...       ...     ...          ...              ...
62373       7584.3   68500.0     698      42519.2                7
62374      10951.6   53600.0     956      42519.2                7
62375       6123.9   82000.0     362      24732.1                7
62376         29.3   94000.0     368      32455.5                1
62383        231.0  100000.0      36      11754.4                1

[8186 rows x 5 columns]

Furthermore, we can turn our remaining values to percentiles.

In [5]:
stop_scores = stop_scores.join(percentiles(stop_scores), rsuffix = '_percent')

In [6]:
stop_scores['Overall_Score'] = (stop_scores.ntrips_percent + stop_scores.Max_Density_percent + stop_scores.walkable_routes_percent)/3
stop_scores.head()

Density   Income  ntrips  Max_Density  walkable_routes  \
stop_code                                                           
10452          0.0      0.0    2865       8089.3                2   
10454       8089.3  63200.0    2865       8089.3                1   
10534      21422.2  36800.0    3150      24666.7               10   
10536        952.5  41600.0    3150      24666.7                5   
10538      24666.7  35600.0    3150      24666.7                5   

           Density_percent  Income_percent  ntrips_percent  \
stop_code                                                    
10452             0.000000        0.000000       87.161545   
10454            31.424276       33.263158       87.161545   
10534            83.218218       19.368421       95.832066   
10536             3.700150       21.894737       95.832066   
10538            95.822035       18.736842       95.832066   

           Max_Density_percent  walkable_routes_percent  Overall_Score  
stop_code                                                               
10452                11.714438                11.764706      36.880230  
10454                11.714438                 5.882353      34.919446  
10534                35.720833                58.823529      63.458810  
10536                35.720833                29.411765      53.654888  
10538                35.720833                29.411765      53.654888

In [12]:
stop_scores = stop_scores.loc[~(stop_scores==0).any(axis=1)]
Overall_vs_income = px.scatter(stop_scores, y = 'Overall_Score', x = 'Income', trendline = 'ols', trendline_options=dict(log_x=True), color = 'Density_percent')

Overall_vs_income.update_traces(marker=dict(size=5))
Overall_vs_income.update_traces(showlegend=True, marker=dict(size=4))

In [8]:
results = px.get_trendline_results(Overall_vs_income)
results = results.iloc[0]["px_fit_results"].summary()
print(results)

                            OLS Regression Results                            
Dep. Variable:                      y   R-squared:                       0.097
Model:                            OLS   Adj. R-squared:                  0.096
Method:                 Least Squares   F-statistic:                     854.4
Date:                Wed, 12 Mar 2025   Prob (F-statistic):          1.53e-178
Time:                        12:53:48   Log-Likelihood:                -31899.
No. Observations:                7993   AIC:                         6.380e+04
Df Residuals:                    7991   BIC:                         6.382e+04
Df Model:                           1                                         
Covariance Type:            nonrobust                                         
                 coef    std err          t      P>|t|      [0.025      0.975]
------------------------------------------------------------------------------
const        168.6240      4.606     36.607      0.0

In [9]:
px.scatter_3d(stop_scores, 'Density', 'Income', 'Overall_Score', color = 'Overall_Score')

In [10]:
all_stop_data = stop_scores.join(stop_data[['stop_name', 'route_name', 'stop_lat', 'stop_lon']])
m = px.scatter_mapbox(all_stop_data, lat='stop_lat', lon='stop_lon', hover_name=all_stop_data.stop_name,
                      hover_data=['Density_percent', 'walkable_routes_percent', 'ntrips_percent', 'Overall_Score'
], color = 'Overall_Score', zoom = 9)
m.update_layout(mapbox_style="open-street-map")
m.update_layout(margin={"r":0,"t":0,"l":0,"b":0})
m.show()

In [11]:
all_stop_data

Density    Income  ntrips  Max_Density  walkable_routes  \
stop_code                                                            
10454       8089.3   63200.0    2865       8089.3                1   
10534      21422.2   36800.0    3150      24666.7               10   
10536        952.5   41600.0    3150      24666.7                5   
10538      24666.7   35600.0    3150      24666.7                5   
10540       8741.1  100000.0    3150      24666.7                6   
...            ...       ...     ...          ...              ...   
62373       7584.3   68500.0     698      42519.2                7   
62374      10951.6   53600.0     956      42519.2                7   
62375       6123.9   82000.0     362      24732.1                7   
62376         29.3   94000.0     368      32455.5                1   
62383        231.0  100000.0      36      11754.4                1   

           Density_percent  Income_percent  ntrips_percent  \
stop_code                                                    
10454            31.424276       33.263158       87.161545   
10534            83.218218       19.368421       95.832066   
10536             3.700150       21.894737       95.832066   
10538            95.822035       18.736842       95.832066   
10540            33.956305       52.631579       95.832066   
...                    ...             ...             ...   
62373            29.462517       36.052632       21.235169   
62374            42.543372       28.210526       29.084271   
62375            23.789342       43.157895       11.013082   
62376             0.113821       49.473684       11.195619   
62383             0.897359       52.631579        1.095224   

           Max_Density_percent  walkable_routes_percent  Overall_Score  \
stop_code                                                                
10454                11.714438                 5.882353      34.919446   
10534                35.720833                58.823529      63.458810   
10536                35.720833                29.411765      53.654888   
10538                35.720833                29.411765      53.654888   
10540                35.720833                35.294118      55.615672   
...                        ...                      ...            ...   
62373                61.573752                41.176471      41.328464   
62374                61.573752                41.176471      43.944831   
62375                35.815542                41.176471      29.335031   
62376                47.000106                 5.882353      21.359359   
62383                17.022016                 5.882353       7.999864   

                                                   stop_name  \
stop_code                                                      
10454      Station Longueuil-Université de Sherbrooke -Zo...   
10534                                Station Côte-des-Neiges   
10536                         Station Université-de-Montréal   
10538                              Station Édouard-Montpetit   
10540                                      Station Outremont   
...                                                      ...   
62373                        Henri-Bourassa / de l'Esplanade   
62374                   Henri-Bourassa / du Bois-de-Boulogne   
62375                              Saint-Laurent / Lighthall   
62376                                        Hickmore / Mega   
62383                             Transcanadienne / Tecumseh   

                                                  route_name   stop_lat  \
stop_code                                                                 
10454                                    [4 Ligne 4 - Jaune]  45.524890   
10534                                    [5 Ligne 5 - Bleue]  45.496846   
10536                                    [5 Ligne 5 - Bleue]  45.503188   
10538                                    [5 Ligne 5 - Bleue]  45.509920   
10540                                    [5 Lig